In [10]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
import torch
from multivae.data.datasets import CUB
import pandas as pd
import os

In [12]:
cub = CUB('../data/CUB/CUB_200_2011/', 'test', captions_per_image=10, im_size=(167, 28))

In [13]:
len(cub.test_filenames.name)

5794

In [14]:
from torch.utils.data import DataLoader

dl = DataLoader(cub, 16)

In [15]:
next(iter(dl)).data["img"].shape

torch.Size([16, 3, 64, 64])

In [17]:
out = cub[10].data["text"]
out

{'tokens': tensor([ 36,  29,  33,  22,   5, 298, 299,  21,  22,   6, 167,  14,   0,   1,
           1,   1,   1,   1]),
 'padding_mask': tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0.])}

In [51]:
out = cub[10].data["img"]
out.shape

AssertionError: (torch.Size([3, 64, 64]), 64)

In [10]:
import matplotlib.pyplot as plt

plt.imshow(torch.movedim(out.data["img"], 0, 2))

AttributeError: 'dict' object has no attribute 'data'

In [100]:
decode_sentence([int(e[0]) for e in out])

['this',
 'bird',
 'has',
 'head',
 'wings',
 'it',
 'white',
 'its',
 'bill',
 'and',
 'a',
 'long',
 'bill',
 'that',
 'and',
 'at',
 'its',
 'tip']

In [11]:
from multivae.models.nn.cub import CubTextEncoder, CubTextDecoderMLP
from multivae.models.jmvae import JMVAEConfig
from pythae.models.base import BaseAEConfig

config = JMVAEConfig(latent_dim=11)

In [12]:
encoder = CubTextEncoder(
    config,
    max_sentence_length=cub.max_words_in_captions,
    ntokens=cub.vocab_size,
    embed_size=512,
    ff_size=128
)#.cuda()

decoder = CubTextDecoderMLP(
    BaseAEConfig(latent_dim=11, input_dim=(cub.max_words_in_captions, cub.vocab_size))
)
#encoder

In [13]:
emb = encoder(input.data['text']).embedding

AttributeError: 'function' object has no attribute 'data'

In [168]:
rec = decoder(emb).reconstruction

In [164]:
torch.argmax(rec, dim=-1).shape

torch.Size([16, 18])

In [169]:
rec.shape

torch.Size([16, 18, 5451])

In [166]:
criterion = torch.nn.NLLLoss()

In [174]:
rec.argmax(dim=-1).shape

torch.Size([16, 18])

In [177]:
criterion(rec.view(-1, cub.vocab_size), input.data['text']['tokens'].view(-1))

tensor(8.6107, grad_fn=<NllLossBackward0>)

In [130]:
input.data['text']["padding_mask"].shape

torch.Size([16, 18, 1])

In [368]:
!pip install matplotlib

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.2/9.2 MB 31.9 MB/s eta 0:00:0000:0100:01
  Using cached kiwisolver-1.4.4-cp38-cp38-manylinux_2_5_x86_64.manylinux1_x86_64.whl (1.2 MB)
  Using cached pyparsing-3.0.9-py3-none-any.whl (98 kB)
  Using cached cycler-0.11.0-py3-none-any.whl (6.4 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 31.5 MB/s eta 0:00:00
  Using cached contourpy-1.0.7-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (300 kB)


In [351]:
cub._load_bbox()

Total filenames:  11788 001.Black_footed_Albatross/Black_Footed_Albatross_0046_18.jpg


{'001.Black_footed_Albatross/Black_Footed_Albatross_0046_18': [60,
  27,
  325,
  304],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0009_34': [139,
  30,
  153,
  264],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0002_55': [14,
  112,
  388,
  186],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0074_59': [112,
  90,
  255,
  242],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0014_89': [70,
  50,
  134,
  303],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0085_92': [33,
  53,
  251,
  395],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0031_100': [7,
  75,
  420,
  262],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0051_796103': [78,
  86,
  333,
  158],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0010_796097': [112,
  76,
  221,
  189],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0025_796057': [27,
  4,
  199,
  201],
 '001.Black_footed_Albatross/Black_Footed_Albatross_0023_796059': [1,
  52,
  342,
  260],
 '001.Black_fo

In [344]:
cub.train_filenames.name[1]

'001.Black_footed_Albatross/Black_Footed_Albatross_0074_59'

In [341]:
len(cub.train_captions[cub.train_filenames.name[1]][0])

11

In [47]:
def decode_sentence(encoding):
    sentence = []
    for enc in encoding:
        sentence.append(cub.idxtoword[enc])

    return sentence

In [349]:
cub.train_captions

defaultdict(list,
            {'001.Black_footed_Albatross/Black_Footed_Albatross_0009_34': [[1,
               2,
               3,
               4,
               5,
               6,
               7,
               6,
               8,
               9,
               10,
               11,
               1,
               12,
               1,
               13,
               14,
               15,
               16,
               6,
               17,
               1,
               18,
               14,
               19,
               4,
               20,
               21,
               9,
               22,
               23,
               24,
               1,
               25,
               6,
               1,
               26],
              [27, 28, 20, 17, 29, 26, 20, 27, 6, 9, 30, 2],
              [1, 31, 4, 28, 32, 17, 25, 33, 6, 17, 34],
              [35,
               28,
               36,
               37,
               38,
               39,
    

In [354]:
import numpy as np
np.random.randint(0, 10)

3

In [345]:
decode_sentence(cub.train_captions[cub.train_filenames.name[1]][9])

['this',
 'bird',
 'has',
 'large',
 'wings',
 'with',
 'stripes',
 'on',
 'the',
 'ends',
 'a',
 'short',
 'tail',
 'a',
 'large',
 'gray',
 'and',
 'white',
 'head',
 'and',
 'a',
 'long',
 'beak',
 'with',
 'a',
 'downward',
 'curve']

In [323]:
a = {"b": 12, "c": 17}

In [324]:
for i in a:
    print(i)

b
c


In [325]:
len(cub.train_captions)

5994

In [317]:
cub.idxtoword

dict_keys([0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219,

In [ ]:
cub.build

In [307]:
len([cap for cap_list in cub.train_captions.values() for cap in cap_list])

59940

In [311]:
cub.build_vocab(cub.train_captions, cub.test_captions)

[[[1017,
   2152,
   21,
   2227,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   2152,
   21,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   1451,
   1749],
  [1017,
   2152,
   21,
   2227,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   2152,
   21,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   1749,
   398],
  [1017,
   2152,
   21,
   2227,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   2152,
   21,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   1017,
   1749],
  [1017,
   2152,
   21,
   2227,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,
   2152,
   21,
   1598,
   1598,
   1417,
   2527,
   2152,
   2491,
   21,
   1417,
   1598,
   36,
   36,


In [293]:
cub.build_voca

defaultdict(list,
            {'001.Black_footed_Albatross/Black_Footed_Albatross_0009_34': [['the',
               'wings',
               'are',
               'brown',
               'long',
               'and',
               'narrow',
               'and',
               'have',
               'white',
               'markings',
               'on',
               'the',
               'secondaries',
               'the',
               'bill',
               'is',
               'blunt',
               'tipped',
               'and',
               'black',
               'the',
               'head',
               'is',
               'light',
               'brown',
               'with',
               'a',
               'white',
               'thin',
               'marking',
               'between',
               'the',
               'eye',
               'and',
               'the',
               'beak'],
              ['grey',
               'bird',
               

In [285]:
list(cub.train_filenames.filename) + list(cub.test_filenames.filename)

['001.Black_footed_Albatross/Black_Footed_Albatross_0009_34',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0074_59',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0014_89',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0031_100',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0051_796103',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0010_796097',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0023_796059',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0040_796066',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0089_796069',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0067_170',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0060_796076',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0056_796078',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0080_796096',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0047_796064',
 '001.Black_footed_Albatross/Black_Footed_Albatross_0017_796098',
 '001.Black_footed_Albatross

In [276]:
cap = cub._load_captions()

In [277]:
len(cap[cub.filenames.filename[0]])

2

In [278]:
cub.filenames.id[0]

1

In [216]:
import pandas as pd
import os


filenames = pd.read_csv(
            os.path.join(cub.data_path, "images.txt"),
            delim_whitespace=True,
            header=None,
            names=['test', "ytfzavd"]
        )
#filenames[1] = filenames[1].str.replace('.jpg', '')
#filenames.columns = ['id', 'filename']
filenames.test

0            1
1            2
2            3
3            4
4            5
         ...  
11783    11784
11784    11785
11785    11786
11786    11787
11787    11788
Name: test, Length: 11788, dtype: int64

In [212]:
cub.train_test_split==1

0      1
0       True  False
1      False   True
2      False  False
3      False   True
4      False   True
...      ...    ...
11783  False   True
11784  False  False
11785  False  False
11786  False   True
11787  False  False

[11788 rows x 2 columns]

In [192]:
cap = cub._load_captions()

In [197]:
cub.filenames

id                                           filename
0          1  001.Black_footed_Albatross/Black_Footed_Albatr...
2          3  001.Black_footed_Albatross/Black_Footed_Albatr...
5          6  001.Black_footed_Albatross/Black_Footed_Albatr...
9         10  001.Black_footed_Albatross/Black_Footed_Albatr...
11        12  001.Black_footed_Albatross/Black_Footed_Albatr...
...      ...                                                ...
11779  11780  200.Common_Yellowthroat/Common_Yellowthroat_00...
11782  11783  200.Common_Yellowthroat/Common_Yellowthroat_00...
11784  11785  200.Common_Yellowthroat/Common_Yellowthroat_00...
11785  11786  200.Common_Yellowthroat/Common_Yellowthroat_00...
11787  11788  200.Common_Yellowthroat/Common_Yellowthroat_00...

[5794 rows x 2 columns]

In [201]:
cub.filenames.filename

0        001.Black_footed_Albatross/Black_Footed_Albatr...
2        001.Black_footed_Albatross/Black_Footed_Albatr...
5        001.Black_footed_Albatross/Black_Footed_Albatr...
9        001.Black_footed_Albatross/Black_Footed_Albatr...
11       001.Black_footed_Albatross/Black_Footed_Albatr...
                               ...                        
11779    200.Common_Yellowthroat/Common_Yellowthroat_00...
11782    200.Common_Yellowthroat/Common_Yellowthroat_00...
11784    200.Common_Yellowthroat/Common_Yellowthroat_00...
11785    200.Common_Yellowthroat/Common_Yellowthroat_00...
11787    200.Common_Yellowthroat/Common_Yellowthroat_00...
Name: filename, Length: 5794, dtype: object

In [182]:
cub.filenames[0].set_axis('test')

TypeError: Index(...) must be called with a collection of some kind, 'test' was passed

In [186]:
cub.filenames.columns = ['test', 'jkendcze']
cub.filenames

test                                           jkendcze
0          1  001.Black_footed_Albatross/Black_Footed_Albatr...
2          3  001.Black_footed_Albatross/Black_Footed_Albatr...
5          6  001.Black_footed_Albatross/Black_Footed_Albatr...
9         10  001.Black_footed_Albatross/Black_Footed_Albatr...
11        12  001.Black_footed_Albatross/Black_Footed_Albatr...
...      ...                                                ...
11779  11780  200.Common_Yellowthroat/Common_Yellowthroat_00...
11782  11783  200.Common_Yellowthroat/Common_Yellowthroat_00...
11784  11785  200.Common_Yellowthroat/Common_Yellowthroat_00...
11785  11786  200.Common_Yellowthroat/Common_Yellowthroat_00...
11787  11788  200.Common_Yellowthroat/Common_Yellowthroat_00...

[5794 rows x 2 columns]

In [164]:
cap[cub.filenames[2]][0]

['light',
 'tan',
 'colored',
 'bird',
 'with',
 'a',
 'white',
 'head',
 'and',
 'an',
 'orange',
 'beak']

In [153]:
dict.fromkeys(cub.filenames)

{'001.Black_footed_Albatross/Black_Footed_Albatross_0046_18': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0002_55': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0085_92': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0025_796057': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0086_796062': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0049_796063': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0006_796065': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0016_796067': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0065_796068': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0042_796071': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0090_796077': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0061_796082': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0008_796083': None,
 '001.Black_footed_Albatross/Black_Footed_Albatross_0033_796086': None,
 '00

In [36]:
files = []
with open("../data/")

with open('../data/CUB/CUB_200_2011/images.txt') as f:
    for line in f.readlines():
        split_name = line.replace('\n', '').replace('.jpg', "").split(" ")
        id = int(split_name[0])
        

In [61]:
import pandas as pd

files = pd.read_csv('../data/CUB/CUB_200_2011/images.txt',  delim_whitespace=True,
                                        header=None)



In [69]:
files[1] =  files[1].str.replace('.jpg', '')[13]

In [71]:
files[0][10]

11

In [72]:
train_test_split = pd.read_csv('../data/CUB/CUB_200_2011/train_test_split.txt',  delim_whitespace=True,
                                        header=None)

In [79]:
len(files)

11788

In [86]:
lsit(files[train_test_split[1]==0][1])

NameError: name 'lsit' is not defined

a

In [88]:
files[1][10]

'001.Black_footed_Albatross/Black_Footed_Albatross_0006_796065'

In [103]:
with open('../data/CUB/text/001.Black_footed_Albatross/Black_Footed_Albatross_0001_796111.txt') as f:
    a = f.readlines()

In [107]:
cub.filenames[1][]

0        001.Black_footed_Albatross/Black_Footed_Albatr...
2        001.Black_footed_Albatross/Black_Footed_Albatr...
5        001.Black_footed_Albatross/Black_Footed_Albatr...
9        001.Black_footed_Albatross/Black_Footed_Albatr...
11       001.Black_footed_Albatross/Black_Footed_Albatr...
                               ...                        
11779    200.Common_Yellowthroat/Common_Yellowthroat_00...
11782    200.Common_Yellowthroat/Common_Yellowthroat_00...
11784    200.Common_Yellowthroat/Common_Yellowthroat_00...
11785    200.Common_Yellowthroat/Common_Yellowthroat_00...
11787    200.Common_Yellowthroat/Common_Yellowthroat_00...
Name: 1, Length: 5794, dtype: object